In [ ]:
# This cell is added by sphinx-gallery
# It can be customized to whatever you like
%matplotlib inline



Borealis Quickstart
===================
.. raw:: html

    <h2 style="font-size:15px;color:white;background-color:#515151;opacity:0.5" >&nbsp;&nbsp;&nbsp;Borealis will only be available to the public until June 2, 2023.<br>&nbsp;&nbsp;&nbsp;Public access to this device will not be available after this date.</h2>

*Authors: Theodor Isacsson and Isaac De Vlugt*

.. related::

    run_advanced_time_domain Advanced time-domain photonic circuits
    run_time_domain Time-domain photonic circuits
    tutorial_borealis_advanced Operating Borealis --- Advanced
    tutorial_borealis_beginner Operating Borealis --- Beginner

In this quickstart, we will show how Xanadu's new Borealis quantum hardware can be programmed in minutes.
Borealis showcases quantum computational advantage, as can be seen in our publication in `Nature <https://xanadu.ai/qca-paper>`__ [[#advantage2022]_] --- meaning that it can compute in seconds quantities that would require years on the fastest available supercomputer.
Its hardware is based on `time-domain multiplexing (TDM) <https://strawberryfields.ai/photonics/demos/run_time_domain.html>`__;
a single squeezed-light source emits batches of 216 time-ordered squeezed-light
pulses that interfere with one another with the help of optical delay loops,
programmable beamsplitters, and phase shifters. To demonstrate quantum computational
advantage, we chose a task that is proven to be computationally hard:
`Gaussian Boson Sampling (GBS) <https://pennylane.ai/qml/demos/tutorial_gbs.html>`__.
We will show you how to run our experiment!


<div class="alert alert-info"><h4>Note</h4><p>If you would like to learn more about Borealis and how to program it in more
    detail, check out our :doc:`Borealis demo for beginners <tutorial_borealis_beginner>`.</p></div>




To start off, we import the necessary packages. Then, by loading
a :class:`device <strawberryfields.Device>` object which contains relevant
and up-to-date information about Borealis, we can retrieve the device
by calling the :class:`device <strawberryfields.Device>`
property on the :class:`RemoteEngine <strawberryfields.RemoteEngine>` object.



In [ ]:
import strawberryfields as sf
import numpy as np

eng = sf.RemoteEngine("borealis")
device = eng.device

A time-domain program is defined by arguments that each quantum
gate applies at each time bin, within the duration of the program.
We're going to use helper functions that will do some heavy lifting for us.
The :func:`borealis_gbs <strawberryfields.tdm.borealis_gbs>` function
will summarize all the necessary information for Strawberry Fields
and our hardware to implement your circuit, then
:func:`get_mode_indices <strawberryfields.tdm.get_mode_indices>`
gives us the number of concurrent modes ``N`` and the mode indices ``n``.




In [ ]:
from strawberryfields.tdm import borealis_gbs, get_mode_indices

gate_args_list = borealis_gbs(device, modes=216, squeezing="high")
delays = [1, 6, 36]
n, N = get_mode_indices(delays)

Finally, we can construct and run the circuit.




In [ ]:
from strawberryfields.ops import Sgate, Rgate, BSgate, MeasureFock

prog = sf.TDMProgram(N)

with prog.context(*gate_args_list) as (p, q):
    Sgate(p[0]) | q[n[0]]
    for i in range(len(delays)):
        Rgate(p[2 * i + 1]) | q[n[i]]
        BSgate(p[2 * i + 2], np.pi / 2) | (q[n[i + 1]], q[n[i]])
    MeasureFock() | q[0]

shots = 10_000
results = eng.run(prog, shots=shots, crop=True)
print(results.samples)

Congratulations for successfully demonstrating quantum computational advantage!




References
~~~~~~~~~~

.. [#advantage2022]

    Madsen, L.S., Laudenbach, F., Askarani, M.F. et al.
    "Quantum computational advantage with a programmable photonic processor",
    `Nature 606, 75-81 <https://www.nature.com/articles/s41586-022-04725-x>`__, 2022.

About the authors
-----------------



.. bio:: Theodor Isacsson
   :photo: ../_static/Theodor.jpg

   Theodor Isacsson is a quantum software developer at Xanadu. He works on the photonics software stack, leading the efforts to expand and maintain packages such as Strawberry Fields and The Walrus.

.. bio:: Isaac De Vlugt
   :photo: ../_static/Isaac.png

   Isaac De Vlugt is a quantum computing educator at Xanadu. His work involves creating accessible quantum computing content for the community, as well as spamming gifs in our Slack channels.

